## Exercise 3.3

### Task

1) Implement a method index(urls), which – given a list of input URLs –
  - downloads each web page (e.g., using the wget commandline tool in linux)
  - strips tags in the resulting HTML (e.g., using the method stripogram.html2text())
  - normalizes the text data (e.g., using string.lower() and the module
stemming.porter2)
  - computes and stores a sparse bag-of-words representation of each page (e.g., using
python dictionaries)

2) run your method to index a list of URLs (list can be found on the course website)
Multimedia Data Mining (SoSe 2016)

3) Implement a method search(query), which – given a sequence of query words – out-
puts a ranked list of web pages in the index based on the cosine distance measure between
the bag-of-words representations of queries and web pages.

4) Search your index with a few queries like “colosseum”, “hungary”, or “tower”. What re-
sults/problems do you observe? State three steps with which you could improve your search
results.

In [1]:
from stripogram import html2text
from stemming import porter2
from collections import Counter
import scipy
from scipy.spatial.distance import cosine

In [22]:
def index(urls):
    # initialize dictionary for storing the representations
    representations = dict()
    
    # downloads each web page
    for url in urls:
        # read the http code from the url
        # N.B.: The "!" character allows you to use commandline commands.
        !wget {url} --output-document=temp.html
        website = ''
        with open('temp.html', 'r') as f:
            website = f.read()
        
        # strip the tags
        information = html2text(website)
        
        # normalize the text data
        # Here we also split the whole text into words.
        words = [porter2.stem(word) for word in information.lower().split()]
        
        # store the words in the representation dictionary
        representations[url] = Counter(words)
    
    return representations


urls = '''http://en.wikipedia.org/wiki/Rome
        http://en.wikipedia.org/wiki/Paris
        http://en.wikipedia.org/wiki/New_York_City
        http://en.wikipedia.org/wiki/Beijing
        http://en.wikipedia.org/wiki/Szeged
        http://en.wikipedia.org/wiki/Florence
        http://en.wikipedia.org/wiki/Z%C3%BCrich
        http://en.wikipedia.org/wiki/Moscow
        http://en.wikipedia.org/wiki/Kaiserslautern
        http://en.wikipedia.org/wiki/Philadelphia
        http://en.wikipedia.org/wiki/Pisa'''.split()

inds = index(urls)

In [38]:
def search(query):
    '''Given a sequence of query words – outputs a ranked list of web pages
    in the index based on the cosine distance measure between
    the bag-of-words representations of queries and web pages.'''
    # choose a vocabulary
    #vocab = list(set(query.split())) # build vocabulary from query (this is faster)
    vocab = list(set([word for url in inds for word in inds[url]])) # build vocabulary from index
    
    # compute the vector representation of the given query
    vec = repr2vec(txt2repr(query), vocab)
    
    # compute distances to all the document vectors
    distances = [(url, cosine(vec, repr2vec(inds[url], vocab))) for url in indexes]
    
    # return the list sorted by ascending cosine distance values
    return sorted(distances, key=lambda x: x[1])
    
    
def txt2repr(text):
    '''Form a bag of words representation from the search query.'''
    return Counter([porter2.stem(word) for word in text.lower().split()])


def repr2vec(representation, vocabulary):
    '''Transform a bag of words representation into a vector.'''
    vec = [representation[word] if word in representation.keys() else 0 for word in vocabulary]
    return vec

In [42]:
search("eiffel tower")

[('http://en.wikipedia.org/wiki/Pisa', 0.99008268526997234),
 ('http://en.wikipedia.org/wiki/Moscow', 0.99481704472011234),
 ('http://en.wikipedia.org/wiki/Paris', 0.99522483938986783),
 ('http://en.wikipedia.org/wiki/Kaiserslautern', 0.99630959877003744),
 ('http://en.wikipedia.org/wiki/Szeged', 0.99734384273043442),
 ('http://en.wikipedia.org/wiki/Z%C3%BCrich', 0.99756372714573471),
 ('http://en.wikipedia.org/wiki/New_York_City', 0.99818612970250364),
 ('http://en.wikipedia.org/wiki/Beijing', 0.9991163051323545),
 ('http://en.wikipedia.org/wiki/Florence', 0.99952676302828414),
 ('http://en.wikipedia.org/wiki/Philadelphia', 0.99969374551807644),
 ('http://en.wikipedia.org/wiki/Rome', 1.0)]

In [41]:
search("hungary")

[('http://en.wikipedia.org/wiki/Szeged', 0.97933994501071464),
 ('http://en.wikipedia.org/wiki/Moscow', 0.99918557715000111),
 ('http://en.wikipedia.org/wiki/Rome', 0.99922282301646326),
 ('http://en.wikipedia.org/wiki/Paris', 0.99935684791453727),
 ('http://en.wikipedia.org/wiki/New_York_City', 0.99971497778054386),
 ('http://en.wikipedia.org/wiki/Philadelphia', 1.0),
 ('http://en.wikipedia.org/wiki/Kaiserslautern', 1.0),
 ('http://en.wikipedia.org/wiki/Beijing', 1.0),
 ('http://en.wikipedia.org/wiki/Z%C3%BCrich', 1.0),
 ('http://en.wikipedia.org/wiki/Pisa', 1.0),
 ('http://en.wikipedia.org/wiki/Florence', 1.0)]

A few problems:
- Search is rather slow (for vocabulary built from index) or inaccurate (for vocabulary built from query). <- See for yourself by modifying the search function.
- Word order doesn't have any influence. (Neither in query nor in documents)
- Stop words can change the results quite drastically.
- Multiword terms are not respected since the query is split into single words.
- ...

Some possible improvements:
- Stop word removal
- Taking website layout into account, e.g. differentiating between headlines and regular text -> weighted count
- Respecting word similarities, e.g. also search for synonyms
- Special handling of named entities
- Estimate website quality by pagerank or other means to protect against spam.
- Fixing typos
- ...